<center><img src="https://github.com/pandas-dev/pandas/raw/main/web/pandas/static/img/pandas.svg" alt="pandas Logo" style="width: 800px;"/></center>

# Pandas Notebook 9: GroupBy + Split/Apply/Combine
---

## Overview
1. Read in and customize a DataFrame, using default row index
1. Split/Apply/Combine
1. Analyze DataFrames produced by the S/A/C technique

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Pandas notebooks 1-8 | Necessary | |

* **Time to learn**: 20 minutes

## Imports

In [ ]:
import pandas as pd
import numpy as np
from datetime import datetime

####  Read in NYSM 5-minute data from a particular day. Use the default row and column index names, but convert the date/time data from `String` to `datetime`. Explicitly set the timezone.

In [ ]:
nysm_data_file = '/spare11/atm533/data/nysm_data_20210902.csv'

timeFormat = "%Y-%m-%d %H:%M:%S UTC"
parseTime = lambda x: datetime.strptime(x, timeFormat)

nysm_data = pd.read_csv(nysm_data_file,parse_dates=['time'], date_parser=parseTime)
nysm_data['time'].dt.tz_localize(tz='UTC')

Remove unwanted columns

In [ ]:
nysm_data.drop(['temp_9m [degC]',
       'avg_wind_speed_prop [m/s]', 'max_wind_speed_prop [m/s]','wind_speed_stddev_prop [m/s]', 'wind_direction_prop [degrees]',
       'wind_direction_stddev_prop [degrees]','wind_speed_stddev_sonic [m/s]','wind_direction_stddev_sonic [degrees]', 'solar_insolation [W/m^2]','snow_depth [cm]', 'frozen_soil_05cm [bit]',
       'frozen_soil_25cm [bit]', 'frozen_soil_50cm [bit]',
       'soil_temp_05cm [degC]', 'soil_temp_25cm [degC]',
       'soil_temp_50cm [degC]', 'soil_moisture_05cm [m^3/m^3]',
       'soil_moisture_25cm [m^3/m^3]', 'soil_moisture_50cm [m^3/m^3]'],inplace=True,axis='columns')

Each dataframe has varying column names. Let's standardize by creating a `dictionary` that will map current column names to common (and in some cases, much shorter) names.

In [ ]:
column_mapping = {'station' : 'STID',
                  'time': 'TIME',
                  'temp_2m [degC]': 'TMPC',
                  'relative_humidity [percent]': 'RELH',
                  'precip_incremental [mm]': 'PRCP',
                  'precip_local [mm]': 'PTOT',
                  'precip_max_intensity [mm/min]': 'PRAT',
                  'avg_wind_speed_sonic [m/s]': 'SPED',
                  'max_wind_speed_sonic [m/s]': 'GUMS',
                  'wind_direction_sonic [degrees]': 'DRCT', 
                  'station_pressure [mbar]': 'PRES',
                  'stid': 'STID',
                  'name': 'NAME',
                  'lat': 'SLAT',
                  'lon': 'SLON',
                  'elevation': 'SELV',
                  'STN':  'STID',
                  'YYMMDD/HHMM': 'TIME'}

Rename the columns according to our dictionary. Then examine each Dataframe to see how they look.

In [ ]:
nysm_data.rename(columns=column_mapping, inplace=True)

In [ ]:
nysm_data.head()

The NYSM data does not contain dewpoint nor sea-level pressure yet. Calculate and create a column for dewpoint; for the purposes of this notebook, we'll not do the SLP conversion.

In [ ]:
tmpc = nysm_data['TMPC']
rh = nysm_data['RELH']

In [ ]:
nysm_data['DWPC'] = 243.04*(np.log(rh/100)+((17.625*tmpc)/(243.04+tmpc)))/(17.625-np.log(rh/100)-((17.625*tmpc)/(243.04+tmpc)))

Let's rearrange the columns into a more logical order.

In [ ]:
colOrder = ['STID','TIME','TMPC','DWPC','RELH','PRES','DRCT','SPED','GUMS','PRCP','PTOT','PRAT']

In [ ]:
nysm_data = nysm_data.reindex(columns=colOrder)

In [ ]:
nysm_data

### Split-Apply-Combine

Now go through the *Split-Apply-Combine* methodology, as defined by Wickham, 2011 and illustrated by McKinney, 2017 (see refs at end of notebook)

<center><img src="../../images/SplitApplyCombine.png" alt="SplitApplyCombine" style="width: 350px;"/></center>

#### Split: Group by station id

In [ ]:
grouped = nysm_data.groupby(['STID'])

In [ ]:
grouped

This has *split* the DataFrame into a Pandas `groupby` object. 

#### Apply and Combine:

Now we *apply* a function on the now-split groups, which then *combines* the group and the values returned by the function into a new DataFrame. 

One built-in `groupby` function is `describe`. It returns a `DataFrame` containing summary statistics, grouped by station, for each column that contains numerical values:

In [ ]:
%time df_stns = grouped.describe() # Depending on the size of your DataFrame, this may take a while

In [ ]:
df_stns

#### Analyze DataFrames produced by the S/A/C technique

<div class="alert alert-block alert-info">
    <b>Tip:</b> This is just another Pandas DataFrame, but with a multiple (i.e. <i>hierarchical</i>) column index ("under the hood", the Multiindexing we demonstrated in Pandas_06 uses `groupby`), and thus we could subset on selected rows and columns / sub-columns from it.</div>

Five-minute and daily accumulated precip:

In [ ]:
df_stns[['PRCP','PTOT']]

Temperature

In [ ]:
df_stns ['TMPC']

What's the maximum 5-minute precip value for the entire NYSM network for that day?

In [ ]:
df_stns['PRCP']['max'].max()

Next we'll select just a couple of rows. We'll re-set the Pandas' defaults so all rows and columns are displayed as a result of this selection; scroll to the right to see all columns:

In [ ]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [ ]:
df_stns.loc[['VOOR','WOLC']]

Next, *split* by station again, *apply* the max/min functions, and *combine* into two DataFrames which contain max and min values for all measured variables:

In [ ]:
df_maxes = nysm_data.groupby(['STID']).max()

In [ ]:
df_mins = nysm_data.groupby(['STID']).min()

In [ ]:
df_maxes

<div class="alert alert-block alert-warning">
<b>Tip:</b> Assign new names for these two series; else they will both be labeled TMPC!</div>

In [ ]:
maxT = df_maxes['TMPC'].rename('TMax')

In [ ]:
minT = df_mins['TMPC'].rename('TMin')

Create a DataFrame out of these two Series, using Pandas' `concat` function.

In [ ]:
pd.concat([maxT,minT],axis='columns')

*Group by* date/time instead of station id, and then apply/combine.

In [ ]:
grouped = nysm_data.groupby(['TIME'])

In [ ]:
df_Maxes = grouped.max()
df_Mins = grouped.min()

In [ ]:
df_Maxes

<div class="alert alert-block alert-warning">
<b>Note:</b> This is a bit deceptive since it looks like YORK had the maximum values for all parameters. But that is because the station ID, <b>STID</b> got sorted as well.</div>

We could construct a DataFrame containing just the max/mins for some selected parameters for each time.

In [ ]:
maxT = df_Maxes[['TMPC','DWPC','SPED','GUMS','PRCP','PTOT','PRAT']]

In [ ]:
maxT

<div class="alert alert-block alert-warning">
<b>Time to re-sort!:</b> If we do not re-sort the index of this DataFrame, the next cell won't work right!</div>

In [ ]:
maxT = maxT.sort_index()

In [ ]:
columnMap = {'TMPC': 'TMax',
             'DWPC': 'TdMax',
             'SPED': 'SPDMax',
             'GUMS': 'GUSTMax',
             'PRCP': 'P5MinMax',
             'PTOT': 'PDayMax',
             'PRAT': 'PRateMax'}
maxT.rename(columns=columnMap, inplace=True)

In [ ]:
maxT

Do the same but for minima (obviously, most of the columns will have 0 as a minimum)

In [ ]:
minT = df_Mins[['TMPC','DWPC','SPED','GUMS','PRCP','PTOT','PRAT']].sort_index()
columnMap = {'TMPC': 'TMin',
             'DWPC': 'TdMin',
             'SPED': 'SPDMin',
             'GUMS': 'GUSTMin',
             'PRCP': 'P5MinMin',
             'PTOT': 'PDayMin',
             'PRAT': 'PRateMin'}
minT.rename(columns=columnMap, inplace=True)

In [ ]:
minT

<div class="alert alert-block alert-info">
<b>Note:</b> We don't see a station ID column, but that's because each max and min likely comes from a different station.</div>

---
## Summary
* Pandas' `groupby` method forms the basis of this library's *split-apply-combine* methodology.

### What's Next?
Next week, we will begin working with gridded datasets, using the [Xarray library](http://xarray.pydata.org/).
## Resources and References
1. [MetPy Monday 99](https://www.youtube.com/watch?v=31k53iHE-yw&list=PLQut5OXpV-0ir4IdllSt1iEZKTwFBa7kO&index=90&ab_channel=Unidata) 
1. [Split/Apply/Combine (Wickham, 2011)](http://dx.doi.org/10.18637/jss.v040.i01)
1. [Ch. 10 notebook from Github Repository for Wes McKinney's Pandas for Data Analysis book](https://github.com/wesm/pydata-book) 